In [1]:
#import libraries 
import pandas as pd
import regex as re 

import matplotlib.pyplot as plt
import plotly.express as px

from ydata_profiling import ProfileReport


from sklearn.cluster import MeanShift
from sklearn.preprocessing import StandardScaler

In [2]:
import plotly.io as pio
pio.renderers.default = "notebook+pdf"

In [3]:
pip install -U kaleido

Note: you may need to restart the kernel to use updated packages.


In [4]:
pd.set_option('display.max_colwidth', None) #show column without truncation

In [5]:
 pd.set_option('display.max_rows', None) #show rows without truncation

This report provides the analysis of credit card report published by London Borough of Barnet. We are given a dataset which is in CSV files. We will start by ,merging  different csv file into pandas dataframe. We will drop the synonymous columns and the irrelavant column. Rename the columns if required and merge the csv files into a dataframe. 

In [6]:
#reads the csv files into a dataframe 
df1=pd.read_csv('Dataset/PCard 1617.csv')
df2=pd.read_csv('Dataset/PCard Transactions 15-16.csv')
df3=pd.read_csv('Dataset/Purchasing Card Data 2014 v1.csv')

In [7]:
#gets first five column of the dataframe 
df1.head()   

Service Area           Account Description  \
0  Adults and Communities         Books-CDs-Audio-Video   
1  Adults and Communities         Books-CDs-Audio-Video   
2  Adults and Communities         Books-CDs-Audio-Video   
3  Adults and Communities  Consumable Catering Supplies   
4  Adults and Communities                     CSG  - IT   

                 Creditor Journal Date  Journal Reference   Total  
0               AMAZON EU   05/12/2016            10510.0   45.00  
1   AMAZON UK MARKETPLACE   05/12/2016            10509.0  426.57  
2  AMAZON UK RETAIL AMAZO   06/12/2016            10524.0  121.38  
3         WWW.ARGOS.CO.UK   01/03/2017            11667.0   78.94  
4   AMAZON UK MARKETPLACE   01/02/2017            10974.0   97.50

In [8]:
df2.head()

Service Area             Account Description  \
0                   Assurance          Miscellaneous Expenses   
1  Children's Family Services          Miscellaneous Expenses   
2  Children's Family Services        E19 - Learning Resources   
3  Children's Family Services  Equipment and Materials Purcha   
4  Children's Family Services                     Subsistence   

                Creditor Journal Date  Journal Reference  Total  
0  43033820 COSTA COFFEE   18/08/2015             5043.0      2  
1  99 PLUS DISCOUNT MART   08/06/2015             4184.0  29.97  
2         99P STORES LTD   07/12/2015             6278.0  34.65  
3         99P STORES LTD   18/08/2015             5041.0  10.72  
4    CHOPSTIX00000000000   21/05/2015             5750.0   33.7

In [9]:
df3.head() 

Service Area             Account Description            Creditor  \
0  Childrens Services                     IT Services       123-REG.CO.UK   
1  Childrens Services                  Other Services  ACCESS EXPEDITIONS   
2  Childrens Services  Equipment and Materials Repair     AFE SERVICELINE   
3  Childrens Services  Equipment and Materials Repair     AFE SERVICELINE   
4  Childrens Services  Building Repairs & Maintenance    ALLSOP & FRANCIS   

  Transaction Date  JV Reference     JV Date  JV Value  
0       23/04/2014            93  20/05/2014    143.81  
1       03/04/2014           111  20/05/2014  6,000.00  
2       02/04/2014             6  20/05/2014    309.38  
3       02/04/2014             7  20/05/2014    218.76  
4       15/04/2014           381  20/05/2014       306

In [10]:
#drop unnecessary columns
df3.drop(columns=['JV Reference','JV Date'],inplace=True)
df1.drop(columns=['Journal Reference'],inplace=True)
df2.drop(columns=['Journal Reference'],inplace=True)

In [11]:
#renaming the synonymous columns
df3.rename(columns={"Transaction Date": "Journal Date", "JV Value": "Total"},inplace=True)

In [12]:
df3.head()

Service Area             Account Description            Creditor  \
0  Childrens Services                     IT Services       123-REG.CO.UK   
1  Childrens Services                  Other Services  ACCESS EXPEDITIONS   
2  Childrens Services  Equipment and Materials Repair     AFE SERVICELINE   
3  Childrens Services  Equipment and Materials Repair     AFE SERVICELINE   
4  Childrens Services  Building Repairs & Maintenance    ALLSOP & FRANCIS   

  Journal Date     Total  
0   23/04/2014    143.81  
1   03/04/2014  6,000.00  
2   02/04/2014    309.38  
3   02/04/2014    218.76  
4   15/04/2014       306

In [13]:
#combining datasets
df= pd.concat([df1,df2,df3],axis=0)

In [14]:
#rows and columns of the dataframe
df.shape

(12589, 5)

In [15]:
#finding the duolicate values
df.duplicated().sum()


726

In [16]:
#drop duplicate values 
df.drop_duplicates(inplace=True)

In [17]:
#percentage of null values 
df.isna().mean()

Service Area           0.000084
Account Description    0.000169
Creditor               0.000169
Journal Date           0.000169
Total                  0.000000
dtype: float64

In [18]:
#number of null values in each column
df.isna().sum()

Service Area           1
Account Description    2
Creditor               2
Journal Date           2
Total                  0
dtype: int64

In [19]:
#dropping null values 
df.dropna(inplace=True)

In [20]:
#information about the count , datatype and memory usuage
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 11861 entries, 0 to 4141
Data columns (total 5 columns):
 #   Column               Non-Null Count  Dtype 
---  ------               --------------  ----- 
 0   Service Area         11861 non-null  object
 1   Account Description  11861 non-null  object
 2   Creditor             11861 non-null  object
 3   Journal Date         11861 non-null  object
 4   Total                11861 non-null  object
dtypes: object(5)
memory usage: 556.0+ KB


In [21]:
#rows and columns after initial data cleaning
df.shape

(11861, 5)

From the df.info() we found out, all the columns in our dataframe are categorical. We will be converting the datetime and total columns to datetime and numeric columns respectively. This will give us the flexibility to perform different calculations and analyse the behaviour of our data. 

In [22]:
#converting total column into numeric 
def convert_total(i):
    output= re.sub(r'[,]',"",i)
    return output 

df['Total'] = df['Total'].apply(lambda x: convert_total(x))
df['Total']=pd.to_numeric(df['Total']) 

In [23]:
#verifying the datatype of total column
df['Total'].dtype

dtype('float64')

In [24]:
#statistical summary of our data 
df.describe()

Total
count  11861.000000
mean     100.880743
std      394.758945
min    -4707.000000
25%       10.000000
50%       28.570000
75%       92.870000
max    15340.800000

From the statistical summary of our data , we can see that we have total of 11861 rows. The maximum value id 15340 while minimum value is -4707.Our mean is 100.88, std is 394 , median is 28, 25% is 10 and 75% is 92.87.

This summary shows that data is widely ranged with significant presence of outliers.This also concludes that mean and std is highly influenced by the presence of outliers. 

In [25]:
#sample of our data 
df.sample(5)

Service Area             Account Description  \
3292  Children's Family Services  Other Transfer Payments to Soc   
1394  Children's Family Services                  Other Services   
2464  Children's Family Services          Miscellaneous Expenses   
554   Children's Family Services                  Other Services   
2159  Children's Family Services                      Food Costs   

                   Creditor Journal Date   Total  
3292       PABULUM CATERING   31/01/2017   20.00  
1394        EBUYER (UK) LTD   08/07/2015  989.97  
2464     WWW.CIMAGLOBAL.COM   18/11/2016  108.00  
554   AMAZON UK MARKETPLACE   26/10/2015   39.98  
2159           WAITROSE 191   13/05/2016    6.33

# Data Understanding

In [26]:
#getting number of unique elements in our columns
for col in df.columns:
    print(col, df[col].nunique())
    print('-----------')

Service Area 24
-----------
Account Description 67
-----------
Creditor 1936
-----------
Journal Date 739
-----------
Total 5880
-----------


From the above output, we can see that we have total of 24 different service areas and 67 different account. 

# Feature Engineering

Feature engineering is the process of extracting the required information from the data. We will extract quarter and year from the journal date column and store it in a new column in our dataframe 

In [27]:
#converting the object value to datetime datatype
df['Journal Date'] = pd.to_datetime(df['Journal Date'], format='%d/%m/%Y')


In [28]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 11861 entries, 0 to 4141
Data columns (total 5 columns):
 #   Column               Non-Null Count  Dtype         
---  ------               --------------  -----         
 0   Service Area         11861 non-null  object        
 1   Account Description  11861 non-null  object        
 2   Creditor             11861 non-null  object        
 3   Journal Date         11861 non-null  datetime64[ns]
 4   Total                11861 non-null  float64       
dtypes: datetime64[ns](1), float64(1), object(3)
memory usage: 556.0+ KB


In [29]:
#creating new column quarter which stores the quarter values 
df['Quarter'] = df['Journal Date'].dt.quarter

In [30]:
df['Quarter'].value_counts(dropna=False)

4    3283
1    2971
3    2918
2    2689
Name: Quarter, dtype: int64

In [31]:
#creating new column year which stores the year values 
df['Year'] = df['Journal Date'].dt.year

In [32]:
df.head()

Service Area           Account Description  \
0  Adults and Communities         Books-CDs-Audio-Video   
1  Adults and Communities         Books-CDs-Audio-Video   
2  Adults and Communities         Books-CDs-Audio-Video   
3  Adults and Communities  Consumable Catering Supplies   
4  Adults and Communities                     CSG  - IT   

                 Creditor Journal Date   Total  Quarter  Year  
0               AMAZON EU   2016-12-05   45.00        4  2016  
1   AMAZON UK MARKETPLACE   2016-12-05  426.57        4  2016  
2  AMAZON UK RETAIL AMAZO   2016-12-06  121.38        4  2016  
3         WWW.ARGOS.CO.UK   2017-03-01   78.94        1  2017  
4   AMAZON UK MARKETPLACE   2017-02-01   97.50        1  2017

# Pandas Profiling 

Pandas profiling is the open source library provided by pandas for quick and easy way to get insights into structure of our data. 

In [33]:
profile = ProfileReport(df, title="Profiling Report")
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

From the pandas profiling we can see that we have imbalanced dataset. Majority of the columns from service area falls under the same category. Some important keywords from our account description are equipment , material , costs while from the creditors are amazon,sainsbury etc. Furthermore it helped us to see the first few and last few columns of our data , missing values and Duplicate rows also the value_counts of each columns. 

# Task 1

In [34]:
service_area_summary= df.groupby(['Year','Quarter','Service Area']).agg(Transaction_Count=('Total', 'count'), Average_Total=('Total', 'mean'),Maximum=('Total','max'),Minimum=('Total','min'),Total_Sum=('Total','sum'))


Summary table of transaction count, average total, maximum , minimum and total sum per each service area per quarter per each year 

In [35]:
service_area_summary

Transaction_Count  Average_Total  \
Year Quarter Service Area                                                       
2014 2       Adults and Communities                         15     252.833333   
             CSG Managed Budget                             20    1608.367000   
             Childrens Services                            875      74.514103   
             Control Accounts                                8      23.838750   
             Deputy Chief Operating Officer                 39      40.544615   
             Governance                                      3    2207.800000   
             Internal Audit & CAFT                           2     203.600000   
             NSCSO                                           1      10.000000   
             Public Health                                   2      -1.175000   
             Strategic Commissioning Board                   1     244.000000   
             Street Scene                                   11      57.280000   
     3       Adults and Communities                          8     321.306250   
             CSG Managed Budget                             12    2045.750000   
             Children's Service DSG                         30      96.591667   
             Childrens Services                            320      73.205781   
             Commercial                                      9     304.783333   
             Deputy Chief Operating Officer                 49      35.270000   
             Education                                      60     130.974167   
             Family Services                               455      66.499099   
             Governance                                      3     392.320000   
             Internal Audit & CAFT                           7      27.564286   
             NSCSO                                           2     222.750000   
             Street Scene                                   16      35.664375   
     4       Adults and Communities                         17     118.195882   
             Assurance                                       3      35.113333   
             CSG Managed Budget                              3    3187.666667   
             Children's Education & Skills                  60     131.156000   
             Children's Family Services                    536      62.107425   
             Children's Service DSG                         32     162.927812   
             Childrens Services                             20      63.205500   
             Commissioning                                  42      73.700238   
             Customer Support Group                         16     322.266875   
             Deputy Chief Operating Officer                 24      35.371250   
             Education                                      35     141.619714   
             Family Services                               273      64.203077   
             Governance                                      1      53.940000   
             Internal Audit & CAFT                           2      58.000000   
             Parking & Infrastructure                        2      46.410000   
             Street Scene                                   12     110.962500   
             Streetscene                                    19      56.486316   
2015 1       Adults and Communities                         11     183.441818   
             Assurance                                       4      16.862500   
             Children's Education & Skills                  76     125.552105   
             Children's Family Services                    586      67.477918   
             Children's Service DSG                         15     202.047333   
             Commissioning                                  28     183.551429   
             Customer Support Group                         14    1350.069286   
             Parking & Infrastructure                        1      28.43000

Service area summary is divided into 4 parts based on year i.e 2014,2015,2016,and 2017. Further , it store the statistical summary : transaction count, average total, maximum, minimum and total sum of each service area based on different quarters. 
This statistical summary is granular which can be helpful to compare and understand the spending  patterns of each service area. This can also be helful for budgeting , financial as well as to understand the trends within each service area. 

In [36]:
service_area_summary[:5]

Transaction_Count  Average_Total  \
Year Quarter Service Area                                                       
2014 2       Adults and Communities                         15     252.833333   
             CSG Managed Budget                             20    1608.367000   
             Childrens Services                            875      74.514103   
             Control Accounts                                8      23.838750   
             Deputy Chief Operating Officer                 39      40.544615   

                                             Maximum  Minimum  Total_Sum  
Year Quarter Service Area                                                 
2014 2       Adults and Communities           815.50    20.00    3792.50  
             CSG Managed Budget              7800.00   -44.99   32167.34  
             Childrens Services              6000.00  -500.00   65199.84  
             Control Accounts                  83.31     3.06     190.71  
             Deputy Chief Operating Officer   354.00     2.15    1581.24

In [37]:
service_area_summary_reset=service_area_summary.reset_index() #reset the index from grouped df

fig = px.bar(service_area_summary_reset, x='Quarter', y='Average_Total', color='Service Area',
             title='Average_Total by Service Area Per Quarter',
             labels={'Average Total': 'Average_Total', 'Service Area': 'Service Area', 'Quarter': 'Quarter'})
fig.update_layout(xaxis={'categoryorder':'total descending'})  # Sort values in descending order
fig.show()

In [38]:
service_area_summary_reset=service_area_summary.reset_index() #reset the index from grouped df

fig = px.bar(service_area_summary_reset, x='Quarter', y='Transaction_Count', color='Service Area',
             title='Transaction Count by Service Area Per Quarter',
             labels={'Average Total': 'Average_Total', 'Service Area': 'Service Area', 'Quarter': 'Quarter'})
fig.update_layout(xaxis={'categoryorder':'total descending'})  # Sort values in descending order
fig.show()

If we look at the summary per year , transaction count slightly increase from 2014 to 2015 to 2016 but it drastically dropped in the year 2017. Similar, pattern can be seen in the average total as well. There is no drastic difference of average total if first 3 years while , average total dropped to less tha 4k from more tha. 14k from year 2016 to 2017. 

In [39]:
service_area_summary_reset=service_area_summary.reset_index() #reset the index from grouped df

fig = px.bar(service_area_summary_reset, x='Service Area', y='Average_Total', color='Quarter',
             title='Average_Total by Service Area Per Quarter',
             labels={'Average Total': 'Average_Total', 'Service Area': 'Service Area', 'Quarter': 'Quarter'})
fig.update_layout(xaxis={'categoryorder':'total descending'})  # Sort values in descending order
fig.show()

From the above diagram we can see that , our diagram is skewed as Customer Service Support has more tha 15k average total while for most of other values it is less than 5k.

Since , our data is skewed , we are dropping first 2 service area to get a closer look on other values. 

In [40]:
#dropping Customer Support Group and CSG Manageemnt Budget to remove the biasness 
service_area_remake= service_area_summary_reset[(service_area_summary_reset['Service Area']!='Customer Support Group') & (service_area_summary_reset['Service Area']!='CSG Managed Budget') ]


In [41]:
service_area_remake_reset=service_area_remake.reset_index()

df['Quarter'] = service_area_remake_reset['Quarter'].astype(str)

fig = px.bar(service_area_remake_reset, x='Service Area', y='Average_Total', color='Quarter',
             title='Transaction Total by Service Area Per Quarter excluding Customer Support Group and CSG Manageemnt Budget',
             labels={'Average Total': 'Average_Total', 'Service Area': 'Service Area', 'Quarter': 'Quarter'})
fig.update_layout(xaxis={'categoryorder':'total descending'}) 
fig.show()

From this bar diagram we can see that average total max for all other values is 2500. It is also visible from the bar diagram that significant transaction happed in quarter 4 and quarter 2.

In [42]:
service_area_remake_reset=service_area_remake.reset_index()

df['Quarter'] = service_area_remake_reset['Quarter'].astype(str)

fig = px.bar(service_area_remake_reset, x='Service Area', y='Maximum', color='Quarter',
             title='Maximum Service Area Per Quarter excluding Customer Support Group and CSG Manageemnt Budget',
             labels={'Average Total': 'Average_Total', 'Service Area': 'Service Area', 'Quarter': 'Quarter'})
fig.update_layout(xaxis={'categoryorder':'total descending'}) 
fig.show()

In [43]:
service_area_remake_reset=service_area_remake.reset_index()

df['Quarter'] = service_area_remake_reset['Quarter'].astype(str)

fig = px.bar(service_area_remake_reset, x='Quarter', y='Maximum', color='Service Area',
             title='Maximum Service Area Per Quarter excluding Customer Support Group and CSG Manageemnt Budget',
             labels={'Average Total': 'Average_Total', 'Service Area': 'Service Area', 'Quarter': 'Quarter'})
fig.update_layout(xaxis={'categoryorder':'total descending'}) 
fig.show()

From this bar diagram gives the maximum value as per service area as per quarter. maximum values is above 30k under the quarter 2. 

In [44]:
df['Quarter'] = service_area_summary_reset['Quarter'].astype(str)

fig = px.bar(service_area_summary_reset, x='Service Area', y='Maximum', color='Quarter',
             title='Maximum Service Area Per Quarter ',
             labels={'Average Total': 'Average_Total', 'Service Area': 'Service Area', 'Quarter': 'Quarter'})
fig.update_layout(xaxis={'categoryorder':'total descending'})  # Sort bars by total transaction count
fig.show()

In [45]:
summary_table_quarter  = df.groupby(['Service Area','Quarter']).agg(Transaction_Count=('Total', 'count'), Average_Total=('Total', 'mean'),Maximum=('Total','max'),Minimum=('Total','min'),Total_Sum=('Total','sum'))


In [46]:
summary_table_quarter_df= pd.DataFrame(summary_table_quarter)

Statistical summary table per service area per quarter 

In [47]:
summary_table_quarter_df

Transaction_Count  Average_Total  \
Service Area                   Quarter                                     
Adults and Communities         1                       32     277.007500   
                               2                       34     189.918235   
                               3                       30     130.414333   
                               4                       38      58.614474   
Assurance                      2                        1       2.000000   
                               3                        1       5.830000   
Children's Education & Skills  1                        3     256.690000   
                               2                        2      18.655000   
                               4                        6     294.831667   
Children's Family Services     1                       22      53.101364   
                               2                       26     112.133846   
                               3                       26      51.562308   
                               4                       22      32.122727   
Children's Service DSG         3                        1     480.000000   
Childrens Services             1                       22      44.190455   
                               2                       25     296.201600   
                               3                       26      84.180769   
                               4                       30      72.387667   
Commissioning                  1                        1     141.250000   
                               3                        1     114.330000   
                               4                       10     114.330000   
Control Accounts               1                        4       9.062500   
                               4                        3      30.173333   
Customer Support Group         3                        1     114.000000   
Deputy Chief Operating Officer 1                        1      10.000000   
                               4                        1      10.000000   
Governance                     1                        1    6388.200000   
Street Scene                   3                        3      26.633333   
                               4                        1     100.000000   

                                        Maximum  Minimum  Total_Sum  
Service Area                   Quarter                               
Adults and Communities         1        1670.30     2.00    8864.24  
                               2        3569.03   -16.22    6457.22  
                               3        3028.20   -15.97    3912.43  
                               4         830.00     4.99    2227.35  
Assurance                      2           2.00     2.00       2.00  
                               3           5.83     5.83       5.83  
Children's Education & Skills  1         374.49   173.58     770.07  
                               2          25.34    11.97      37.31  
                               4         500.00     7.19    1768.99  
Children's Family Services     1         235.70   -10.64    1168.23  
                               2         751.75    -9.25    2915.48  
                               3         341.33  -751.75    1340.62  
                               4         107.95     2.99     706.70  
Children's Service DSG         3         480.00   480.00     480.00  
Childrens Services             1         349.73   -23.40     972.19  
                               2        6000.00     0.99    7405.04  
                               3         600.00    -6.90    2188.70  
                               4         500.00     1.90    2171.63  
Commissioning                  1         141.25   141.25     141.25  
                               3         114.33   114.33     114.33  
                               4         114.33   114.33    1143.30  
Control Accounts               1          15.99     3.99      36.25  
   

The table gives the comprehensive summary of transaction for each service area across four different quarters. This table is also a base for creating visual representation. This can help the auditor to identify the trends, visualize the anomalies and understand the underlying pattern of data.  We have the visual representation of transaction count,average total and maximum for each individual service areas across the quarters. Users can get more information of the data, by hovering over the graph.

In [48]:
summary = summary_table_quarter_df.reset_index()

# Visualize transaction count by quarter for each service area
for service_area in summary['Service Area'].unique():
    service_area_data = summary[summary['Service Area'] == service_area]
    fig = px.bar(service_area_data, x='Quarter', y='Transaction_Count',text_auto=True,
             title=f'Transactions by Quarter - {service_area}',
             labels={'Average Total': 'Average_Total', 'Service Area': 'Service Area', 'Quarter': 'Quarter'})
    fig.show()


In [49]:
# Group by 'Service Area' and 'Quarter', and calculate statistics
summary = summary_table_quarter_df.reset_index()

# Visualize transactions by quarter for each service area
for service_area in summary['Service Area'].unique():
    service_area_data = summary[summary['Service Area'] == service_area]
    fig = px.bar(service_area_data, x='Quarter', y='Average_Total',text_auto=True,
             title=f'Transactions by Average - {service_area}',
             labels={'Average Total': 'Average_Total', 'Service Area': 'Service Area', 'Quarter': 'Quarter'})
    fig.show()


In [50]:
# Group by 'Service Area' and 'Quarter', and calculate statistics
summary = summary_table_quarter_df.reset_index()

# Visualize transactions by quarter for each service area
for service_area in summary['Service Area'].unique():
    service_area_data = summary[summary['Service Area'] == service_area]
    fig = px.bar(service_area_data, x='Quarter', y='Maximum',
             title=f'Maximum Transactions by service_area per quarter for  - {service_area}',
             barmode='group',text_auto=True)
    fig.show()


# Task 2

# Data Preparation

In [51]:
#group together data by service area , accound description and year
dfs= df.groupby(['Service Area','Account Description','Year']).agg(Total_Sum=('Total','sum'))

In [52]:
#reset the index of grouped data 
dfsn= dfs.reset_index()

In [53]:
#function to visualize the spending behaviour
def view_spike(service_name):
    return(px.line(dfsn[dfsn['Service Area']==service_name],x='Year',y='Total_Sum',text="Year",color='Account Description'))   

In [54]:
view_spike('Assurance')

In [55]:
view_spike("Children's Education & Skills")

The attempt to understand the spending behaviour trends based on service area and account description from the chart proved to be vague and obscure. Alternatively , z-score analysis is performed to understand the spending behaviour of service area and account.

In [56]:
#grouping data based on both quarter and year
Acc_spike= df.groupby(['Service Area','Account Description','Quarter','Year']).agg(Total_Expense=('Total', 'sum')).sort_values(by='Total_Expense',ascending=False)

In [57]:
Acc_spike['Total_Expense']=Acc_spike['Total_Expense'].astype(int)

In [58]:
#reset the index of grouped dataframe 
Acc_spike.reset_index()

#calculate mean and standard deviation to determine z score 
total_exp_mean = Acc_spike['Total_Expense'].mean()
total_exp_std = Acc_spike['Total_Expense'].std()

#calculate the z score
Acc_spike['z_score'] = (Acc_spike['Total_Expense'] - int(total_exp_mean))/int(total_exp_std)

#determining our threshold value
th = 1.5 

#creating the column to store the z-value 
Acc_spike['spike'] = Acc_spike['z_score'].abs() > th

#creating the df to display the spiked data 
spikes = Acc_spike[Acc_spike['spike']]

#display the dataframe
spikes

Total_Expense  \
Service Area               Account Description            Quarter Year                  
Governance                 Other Services                 1       2014           6388   
Childrens Services         Other Services                 2       2014           6000   
Adults and Communities     Other Agencies - Third Party P 1       2016           4125   
                           Electricity                    2       2017           3569   
                           Rents                          3       2016           3028   
                           Other Agencies - Third Party P 1       2017           2354   
Children's Family Services Equipment and Materials Purcha 2       2015           1994   

                                                                         z_score  \
Service Area               Account Description            Quarter Year             
Governance                 Other Services                 1       2014  6.189441   
Childrens Services         Other Services                 2       2014  5.787785   
Adults and Communities     Other Agencies - Third Party P 1       2016  3.846791   
                           Electricity                    2       2017  3.271222   
                           Rents                          3       2016  2.711180   
                           Other Agencies - Third Party P 1       2017  2.013458   
Children's Family Services Equipment and Materials Purcha 2       2015  1.640787   

                                                                        spike  
Service Area               Account Description            Quarter Year         
Governance                 Other Services                 1       2014   True  
Childrens Services         Other Services                 2       2014   True  
Adults and Communities     Other Agencies - Third Party P 1       2016   True  
                           Electricity                    2       2017   True  
                           Rents                          3       2016   True  
                           Other Agencies - Third Party P 1       2017   True  
Children's Family Services Equipment and Materials Purcha 2       2015   True

Z-score tells us how much standard deviation far is data from the mean of the distribution. Positive z-score shows value is above the mean while the negative score shows data is below the mean value. 

In our data, z-score can tell how much significant our data deviates from the mean value which also indicates spike or permanent increase in spending behaviour. From the above diagram we can tell that , Service Area : Governance and Childrens Service under other services in 2014 quarter 2 has z score of 5.84 and 5.46 respectively which shows significant increase from the mean value indicating spike. Similarly , we can see spike in adults and communities in the year 2016 and 2017 suggesting noteworthy outliers. 

# Task 3

In [59]:
#groupe data based on creditor and account description
Acc_creditor = df.groupby(['Creditor', 'Account Description']).size().reset_index(name='Count')

print('Shape of df:', Acc_creditor.shape)
print('Shape with count equals to 1:', Acc_creditor[Acc_creditor['Count']==1].shape)
print('Shape with count less than 10:', Acc_creditor[Acc_creditor['Count']<5].shape)
print('Shape with count greater than 10:', Acc_creditor[Acc_creditor['Count']>5].shape)

Shape of df: (2875, 3)
Shape with count equals to 1: (1758, 3)
Shape with count less than 10: (2497, 3)
Shape with count greater than 10: (317, 3)


In [60]:
#display 10 data from Acc_creditor dataframe 
Acc_creditor[:10]

Creditor             Account Description  Count
0                 ARGOS  Other Transfer Payments to Soc      1
1   COFFEE REPUBLIC WOO                      Food Costs      1
2            COSTCUTTER                      Food Costs      1
3       H HARIA CHEMIST  Other Transfer Payments to Soc      1
4                LEWISS  Equipment and Materials Purcha      1
5     SAINSBURYS S/MKTS                      Food Costs      1
6                SAVERS  Other Transfer Payments to Soc      1
7      STUDEN PHOTOCARD             Travelling Expenses      2
8     Sainsburys S/mkts                      Food Costs      1
9        TESCO PFS 2473                      Food Costs      2

In [61]:
#checks for duplicate entries 
misclassified_creditors = Acc_creditor[Acc_creditor['Creditor'].duplicated(keep=False)]
misclassified_creditors.shape

(1413, 3)

By executing above code we can identify instances where the same Creditor value appears in multiple Account description, which suggests the potential misclassification of transaction in our data. The duplicated function along with the parameter keep=False returns boolean value where true indicates the presence of more than one creditor value in our grouped dataframe. 

In [62]:
misclassified_creditors[:20]

Creditor             Account Description  Count
15       123-REG.CO.UK                     IT Services      1
16       123-REG.CO.UK                   Subscriptions      1
22      99P STORES LTD        E19 - Learning Resources      1
23      99P STORES LTD  Equipment and Materials Purcha      2
25      A&Y LOCKSMITHS  Clothing - Protective Clothing      1
26      A&Y LOCKSMITHS          Miscellaneous Expenses      1
35       ABLE GROUP UK  Private Contractors - Third Pa      1
36       ABLE GROUP UK           Professional Services      1
38  ACCESS EXPEDITIONS  Equipment and Materials Purcha      1
39  ACCESS EXPEDITIONS                  Other Services      1
50     AFE SERVICELINE  Equipment and Materials Purcha      1
51     AFE SERVICELINE  Equipment and Materials Repair     10
52     AFE SERVICELINE  Private Contractors - Third Pa      2
54  AFFINITY WATER LTD  Equipment and Materials Purcha      1
55  AFFINITY WATER LTD          Miscellaneous Expenses      1
56  AFFINITY WATER LTD                  Water Services      1
58                ALDI                      Food Costs      1
59                ALDI                        Training     12
61    ALEXANDRA PALACE                  Other Services      1
62    ALEXANDRA PALACE                      Venue Hire      1

In [63]:
df[df['Creditor']=='STUDEN PHOTOCARD'] #total sample data 

Service Area             Account Description  \
107           Childrens Services             Travelling Expenses   
256           Childrens Services             Travelling Expenses   
257           Childrens Services             Travelling Expenses   
999           Childrens Services             Travelling Expenses   
1336          Childrens Services  Other Transfer Payments to Soc   
1964             Family Services             Travelling Expenses   
2825  Children's Family Services             Travelling Expenses   
3175  Children's Family Services             Travelling Expenses   
3556  Children's Family Services  Other Transfer Payments to Soc   

              Creditor Journal Date  Total Quarter  Year  
107   STUDEN PHOTOCARD   2014-04-02   10.0       4  2014  
256   STUDEN PHOTOCARD   2014-04-24   10.0     NaN  2014  
257   STUDEN PHOTOCARD   2014-04-21   10.0     NaN  2014  
999   STUDEN PHOTOCARD   2014-06-16   10.0     NaN  2014  
1336  STUDEN PHOTOCARD   2014-07-16   10.0     NaN  2014  
1964  STUDEN PHOTOCARD   2014-09-30   10.0     NaN  2014  
2825  STUDEN PHOTOCARD   2014-11-12   10.0     NaN  2014  
3175  STUDEN PHOTOCARD   2014-12-15   10.0     NaN  2014  
3556  STUDEN PHOTOCARD   2015-01-09   10.0     NaN  2015

In [64]:
misclassified_creditors[misclassified_creditors['Creditor']=='STUDEN PHOTOCARD'] #misclassified 

Creditor             Account Description  Count
2052  STUDEN PHOTOCARD  Other Transfer Payments to Soc      2
2053  STUDEN PHOTOCARD             Travelling Expenses      7

# Task 4

There are different clustering techniques which can be used to cluster our data to understand the underlying pattern . One of the most common clustering technique is KMeans. KMeans require the number of clusters to be defined prior while the another technique mean shift clustering doesnot require to specify the number of clusters. The major challenge with KMeans is accurately defining the number of clusters hence I chose mean shift clustering technique. 
Mean shift clustering is the density based techniques which can identify the number of clusters with irregular shapes. 

In [65]:
scaler = StandardScaler()
clustering_df = df.groupby('Service Area').agg(Transaction_Count=('Total', 'count')).reset_index()
clustering_df_scaled = scaler.fit_transform(clustering_df[['Transaction_Count']])

# Applying Mean Shift clustering
bandwidths = [0.05,0.08]
for bandwidth in bandwidths:
    meanshift = MeanShift(bandwidth=bandwidth)
    clustering_df['Cluster'] = meanshift.fit_predict(clustering_df_scaled)

# Results
clustering_df

Service Area  Transaction_Count  Cluster
0           Adults and Communities                273        1
1                        Assurance                340        1
2               CSG Managed Budget                 35        0
3    Children's Education & Skills                467        1
4       Children's Family Services               7435        2
5           Children's Service DSG                275        1
6               Childrens Services               1215        3
7                       Commercial                  9        0
8                    Commissioning                383        1
9                 Control Accounts                  8        0
10          Customer Support Group                110        0
11  Deputy Chief Operating Officer                112        0
12                       Education                 95        0
13                 Family Services                728        4
14                      Governance                  7        0
15                             HRA                  1        0
16           Internal Audit & CAFT                 11        0
17                           NSCSO                  3        0
18        Parking & Infrastructure                 12        0
19                   Public Health                  3        0
20             Regional Enterprise                  6        0
21   Strategic Commissioning Board                  1        0
22                    Street Scene                 39        0
23                     Streetscene                293        1

In [66]:
clustering_df['Cluster'].value_counts()

0    15
1     6
2     1
3     1
4     1
Name: Cluster, dtype: int64

In [67]:
clustering_df.loc[clustering_df['Cluster'].isin([3, 4]), 'Cluster'] = 2

In [68]:
#values in each cluster 
clustering_df['Cluster'].value_counts()

0    15
1     6
2     3
Name: Cluster, dtype: int64

Our algorithm success fully classified our service area into 5 clusters. Since the last 3 clusters had only 1 value in each of them i merged all three of them for simplicity. We have total of three cluster where , cluster 1 has 15 service area, 2 has 6 and 3 has 3 service areas. Service area with similar transactional behaviour are clustered together.The details of each cluster is shown below with visual representation. 

In [69]:
cluster1= clustering_df[clustering_df['Cluster']==0].sort_values(by='Transaction_Count', ascending=False)
cluster1

Service Area  Transaction_Count  Cluster
11  Deputy Chief Operating Officer                112        0
10          Customer Support Group                110        0
12                       Education                 95        0
22                    Street Scene                 39        0
2               CSG Managed Budget                 35        0
18        Parking & Infrastructure                 12        0
16           Internal Audit & CAFT                 11        0
7                       Commercial                  9        0
9                 Control Accounts                  8        0
14                      Governance                  7        0
20             Regional Enterprise                  6        0
17                           NSCSO                  3        0
19                   Public Health                  3        0
15                             HRA                  1        0
21   Strategic Commissioning Board                  1        0

In [70]:
cluster2= clustering_df[clustering_df['Cluster']==1].sort_values(by='Transaction_Count', ascending=False)
cluster2

Service Area  Transaction_Count  Cluster
3   Children's Education & Skills                467        1
8                   Commissioning                383        1
1                       Assurance                340        1
23                    Streetscene                293        1
5          Children's Service DSG                275        1
0          Adults and Communities                273        1

In [71]:
cluster3= clustering_df[clustering_df['Cluster']==2].sort_values(by='Transaction_Count', ascending=False)
cluster3.reset_index()

index                Service Area  Transaction_Count  Cluster
0      4  Children's Family Services               7435        2
1      6          Childrens Services               1215        2
2     13             Family Services                728        2

In [72]:
fig = px.bar(cluster1.reset_index(), x='Service Area', y='Transaction_Count', color='Transaction_Count',
             title='Cluster 1',
             labels={'Average Total': 'Average_Total', 'Service Area': 'Service Area'})
fig.show()

In [73]:
fig = px.bar(cluster2.reset_index(), x='Service Area', y='Transaction_Count', color='Transaction_Count',
             title='Cluster 2',
             labels={'Average Total': 'Average_Total', 'Service Area': 'Service Area'})
fig.show()

In [74]:
fig = px.bar(cluster3.reset_index(), x='Service Area', y='Transaction_Count', color='Transaction_Count',
             title='Cluster 3',
             labels={'Average Total': 'Average_Total', 'Service Area': 'Service Area', 'Quarter': 'Quarter'})
fig.show()

# Task 5 

In [75]:
df.head()

Service Area           Account Description  \
0  Adults and Communities         Books-CDs-Audio-Video   
1  Adults and Communities         Books-CDs-Audio-Video   
2  Adults and Communities         Books-CDs-Audio-Video   
3  Adults and Communities  Consumable Catering Supplies   
4  Adults and Communities                     CSG  - IT   

                 Creditor Journal Date   Total Quarter  Year  
0               AMAZON EU   2016-12-05   45.00       2  2016  
1   AMAZON UK MARKETPLACE   2016-12-05  426.57       2  2016  
2  AMAZON UK RETAIL AMAZO   2016-12-06  121.38       2  2016  
3         WWW.ARGOS.CO.UK   2017-03-01   78.94       2  2017  
4   AMAZON UK MARKETPLACE   2017-02-01   97.50       2  2017

In [76]:
#Anomaly detection based on each service area 
df['Service Area'].unique() #gives us the name of each service area

array(['Adults and Communities', 'Assurance',
       "Children's Education & Skills", "Children's Family Services",
       "Children's Service DSG", 'Commissioning',
       'Customer Support Group', 'HRA', 'Parking & Infrastructure',
       'Public Health', 'Regional Enterprise', 'Streetscene',
       'Childrens Services', 'Control Accounts', 'Street Scene',
       'Governance', 'Deputy Chief Operating Officer',
       'Internal Audit & CAFT', 'NSCSO', 'CSG Managed Budget',
       'Strategic Commissioning Board', 'Family Services', 'Education',
       'Commercial'], dtype=object)

IQR stands for Interquartile range. It is the range between the quartile1(Q1) and quartile3(Q3)and is commonly used to identify the outliers or anomalies in the data. It is also way to understand the distribution of our data , by diving it into four parts. 

Outliers in this case are those values which are below(q1 - (1.5 * iqr)) i.e lower_whisker and above 
(q3 + (1.5 * iqr)) i.e upper_whisker. 

"Calculate_whiskers" function takes the dataframe and columnname and returns the value of upper whisker and lower whisker


In [77]:
#determining the outliers using IQR technique 
def calculate_whiskers(df,colname): 
    q1 = df[colname].quantile(.25)
    q3 = df[colname].quantile(.75)
    iqr = q3 - q1
    w_multiplier = 1.5 * iqr
    lower_whisker = q1 - w_multiplier
    upper_whisker = q3 + w_multiplier
    return upper_whisker, lower_whisker

"find_outliers" function takes the upper whisker and lower whisker: and returns the dataframe of outliers. 


In [78]:
def find_outliers(df):
    uw,lw = calculate_whiskers(df, 'Total')
    outliers_df = df[(df['Total'] < lw) | (df['Total'] > uw)]
    return outliers_df

We are implementing the for loop to pass the value of each service area from our dataframe. outliers_df_final is the final dataframe which is created by concatenating outlier values from each service area 

In [79]:
outliers_df_final = pd.DataFrame()
for service_area in df['Service Area'].unique():
    service_area_df = df[df['Service Area'] == service_area]
    outliers_df_final = pd.concat([outliers_df_final, find_outliers(service_area_df)])


In [80]:
outliers_df_final.shape #total number of outlier values in our dataframe

(1180, 7)

In [81]:
def get_samples(service_area):
    if len(service_area) >= 10:
        return service_area.sample(n=10)
    else:
        return service_area

# Apply get_samples on grouped service area
select_val = outliers_df_final.groupby('Service Area', group_keys=False).apply(get_samples)

if len(select_val) > 150:
    select_val = select_val.sample(n=150)

# Create a new DataFrame with the selected values
selected_df = pd.DataFrame(select_val)

# Reset index of the DataFrame
selected_df.reset_index(drop=True, inplace=True)

# Display the new DataFrame
selected_df[['Service Area','Account Description','Creditor','Journal Date','Total']].sort_values(by='Service Area')

Service Area             Account Description  \
0            Adults and Communities                        Training   
1            Adults and Communities                        Training   
2            Adults and Communities                        Training   
3            Adults and Communities  Other Agencies - Third Party P   
4            Adults and Communities                        Training   
5            Adults and Communities                        Training   
6            Adults and Communities                        Training   
7            Adults and Communities             Other Vehicle Costs   
8            Adults and Communities                        Training   
9            Adults and Communities                        Training   
19                        Assurance           Fixtures and fittings   
18                        Assurance             Other Vehicle Costs   
17                        Assurance           Vehicle Running Costs   
15                        Assurance          Pool Transport Charges   
16                        Assurance  Equipment and Materials Purcha   
13                        Assurance          Miscellaneous Expenses   
12                        Assurance          Miscellaneous Expenses   
11                        Assurance                        Training   
10                        Assurance                        Training   
14                        Assurance                        Training   
20               CSG Managed Budget            Legal and Court Fees   
27    Children's Education & Skills           Books-CDs-Audio-Video   
26    Children's Education & Skills             Travelling Expenses   
25    Children's Education & Skills                      Food Costs   
23    Children's Education & Skills                        Training   
22    Children's Education & Skills             Conference Expenses   
21    Children's Education & Skills             Conference Expenses   
24    Children's Education & Skills                      Food Costs   
34       Children's Family Services  Equipment and Materials Repair   
37       Children's Family Services  Other Transfer Payments to Soc   
36       Children's Family Services  Equipment and Materials Purcha   
35       Children's Family Services  Equipment and Materials Purcha   
33       Children's Family Services  Other Transfer Payments to Soc   
31       Children's Family Services                Telephones Calls   
30       Children's Family Services                     Advertising   
29       Children's Family Services  Private Contractors - Third Pa   
28       Children's Family Services                      Food Costs   
32       Children's Family Services  Education CFR Administrative S   
46           Children's Service DSG  Equipment and Materials Purcha   
47           Children's Service DSG             Conference Expenses   
45           Children's Service DSG  Equipment and Materials Purcha   
44           Children's Service DSG           Books-CDs-Audio-Video   
43           Children's Service DSG  Equipment and Materials Purcha   
42           Children's Service DSG           Books-CDs-Audio-Video   
41           Children's Service DSG             Travelling Expenses   
40           Children's Service DSG           Books-CDs-Audio-Video   
39           Children's Service DSG                        Training   
38           Children's Service DSG  Equipment and Materials Purcha   
56               Childrens Services  Equipment and Materials Purcha   
55               Childrens Services                      Food Costs   
54               Childrens Services    Consumable Catering Supplies   
53               Childrens Services                  Other Services   
48               Childrens Services                      Food Costs   
51               Childrens Services                      Food Costs   
50               Childrens Services                      Food Costs   
49               Childrens Services            

In [82]:
#extracting only few hundred outliers from the entire dataframe 
selected_df.shape

(119, 7)

In [83]:
#count of service area in our selected dataframe for anomaly detection 
selected_df['Service Area'].nunique()

19

This document provides the comprehensive summary of quarterly transaction of each summary data including the detailed visual representation. Using the z-score document has analysed the instances of spikes and permanent increase in transaction behaviour. By understanding how creditors are classified, document has successfully classified the misclassified creditors. The clustering technique is implemented to classify the similar service area into a same cluster based on their transaction pattern.This can help in resource allocation and budget planning. Finally , the outlier detection using the IQR technique can be the starting point to investigate the potential irregularities and suspicious activities. 